In [1]:
import datetime


def calculate_age(taken, dob):
    birth = datetime.fromordinal(max(int(dob) - 366, 1))

    # assume the photo was taken in the middle of the year
    if birth.month < 7:
        return taken - birth.year
    else:
        return taken - birth.year - 1

In [2]:
import os
from scipy.io import loadmat

def load_data(wiki_dir, dataset='wiki'):
    # Load the wiki.mat file
    meta = loadmat(os.path.join(wiki_dir, "{}.mat".format(dataset)))

    # Load the list of all files
    full_path = meta[dataset][0, 0]["full_path"][0]

    # List of Matlab serial date numbers
    dob = meta[dataset][0, 0]["dob"][0]

    # List of years when photo was taken
    photo_taken = meta[dataset][0, 0]["photo_taken"][0]  # year

    # Calculate age for all dobs
    age = [calculate_age(photo_taken[i], dob[i]) for i in range(len(dob))]

    # Create a list of tuples containing a pair of an image path and age
    images = []
    age_list = []
    for index, image_path in enumerate(full_path):
        images.append(image_path[0])
        age_list.append(age[index])

    # Return a list of all images and respective age
    return images, age_list

In [3]:
import math
import os
import time
from datetime import datetime

import matplotlib.pyplot as plt
import numpy as np
import tensorflow as tf
from keras import Input, Model
#from keras.applications import InceptionResNetV2
from keras.callbacks import TensorBoard
from keras.layers import (
    Conv2D, Flatten, Dense, BatchNormalization, Reshape, concatenate, LeakyReLU, Lambda,
    Conv2DTranspose, Activation, UpSampling2D, Dropout) #, Backend as K)
from keras import backend as K
#from keras.optimizers import Adam
#from keras.utils import to_categorical
from keras_preprocessing import image
from scipy.io import loadmat

In [4]:
input_layer = Input(shape=(64, 64, 3))

In [5]:
# 1st Convolutional Block
# first convolution block, which contains a 2D convolution layer with an activation function

enc = Conv2D(filters=32, kernel_size=5, strides=2, padding='same')(input_layer)
enc = LeakyReLU(alpha=0.2)(enc)

2022-02-18 22:21:28.463721: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:939] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-02-18 22:21:28.488818: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:939] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-02-18 22:21:28.488945: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:939] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-02-18 22:21:28.489424: I tensorflow/core/platform/cpu_feature_guard.cc:151] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  SSE4.1 SSE4.2 AVX AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropri

In [6]:
# add three more convolution blocks, each one of which contains a 2-D convolution layer followed by a batch normalization layer and an activation function

# 2nd Convolutional Block
enc = Conv2D(filters=64, kernel_size=5, strides=2, padding='same')(enc)
enc = BatchNormalization()(enc)
enc = LeakyReLU(alpha=0.2)(enc)

# 3rd Convolutional Block
enc = Conv2D(filters=128, kernel_size=5, strides=2, padding='same')(enc)
enc = BatchNormalization()(enc)
enc = LeakyReLU(alpha=0.2)(enc)

# 4th Convolutional Block
enc = Conv2D(filters=256, kernel_size=5, strides=2, padding='same')(enc)
enc = BatchNormalization()(enc)
enc = LeakyReLU(alpha=0.2)(enc)

In [7]:
# flatten the output from the last convolution block

# Flatten layer
enc = Flatten()(enc)

In [8]:
# add a dense (fully-connected) layer followed by a batch normalization layer and an activation function

# 1st Fully Connected Layer
enc = Dense(4096)(enc)
enc = BatchNormalization()(enc)
enc = LeakyReLU(alpha=0.2)(enc)

In [9]:
# add the second dense (fully-connected) layer

# Second Fully Connected Layer
enc = Dense(100)(enc)

In [10]:
# create a Keras model and specify the inputs and outputs for the encoder network

# Create a model
model = Model(inputs=[input_layer], outputs=[enc])

In [11]:
def build_encoder():
    """
    Encoder Network
    :return: Encoder model
    """
    input_layer = Input(shape=(64, 64, 3))

    # 1st Convolutional Block
    enc = Conv2D(filters=32, kernel_size=5, strides=2, padding='same')(input_layer)
    enc = LeakyReLU(alpha=0.2)(enc)

    # 2nd Convolutional Block
    enc = Conv2D(filters=64, kernel_size=5, strides=2, padding='same')(enc)
    enc = BatchNormalization()(enc)
    enc = LeakyReLU(alpha=0.2)(enc)

    # 3rd Convolutional Block
    enc = Conv2D(filters=128, kernel_size=5, strides=2, padding='same')(enc)
    enc = BatchNormalization()(enc)
    enc = LeakyReLU(alpha=0.2)(enc)

    # 4th Convolutional Block
    enc = Conv2D(filters=256, kernel_size=5, strides=2, padding='same')(enc)
    enc = BatchNormalization()(enc)
    enc = LeakyReLU(alpha=0.2)(enc)

    # Flatten layer
    enc = Flatten()(enc)

    # 1st Fully Connected Layer
    enc = Dense(4096)(enc)
    enc = BatchNormalization()(enc)
    enc = LeakyReLU(alpha=0.2)(enc)

    # Second Fully Connected Layer
    enc = Dense(100)(enc)

    # Create a model
    model = Model(inputs=[input_layer], outputs=[enc])
    
    return model

In [12]:
def build_generator():
    """
    The generator network is a CNN that takes a 100-dimensional vector z and generates an image with a dimension of (64, 64, 3)
    Create a Generator Model with hyperparameters values defined as follows
    :return: Generator model
    """
    
    # Start by creating the two input layers to the generator network
    latent_dims = 100
    num_classes = 6

    input_z_noise = Input(shape=(latent_dims,))
    input_label = Input(shape=(num_classes,))

    # concatenate the inputs along the channel dimension. will generate a concatenated tensor
    x = concatenate([input_z_noise, input_label])

    # add a dense (fully connected) block
    x = Dense(2048, input_dim=latent_dims + num_classes)(x)
    x = LeakyReLU(alpha=0.2)(x)
    x = Dropout(0.2)(x)

    # add the second dense (fully-connected) block
    x = Dense(256 * 8 * 8)(x)
    x = BatchNormalization()(x)
    x = LeakyReLU(alpha=0.2)(x)
    x = Dropout(0.2)(x)

    # reshape the output from the last dense layer to a three-dimensional tensor with a dimension of (8, 8, 256). will generate a tensor of a dimension of (batch_size, 8, 8, 256)
    x = Reshape((8, 8, 256))(x)

    # add an upsampling block that contains an upsampling layer followed by a 2-D convolution layer and a batch normalization layer
    x = UpSampling2D(size=(2, 2))(x)
    x = Conv2D(filters=128, kernel_size=5, padding='same')(x)
    x = BatchNormalization(momentum=0.8)(x)
    x = LeakyReLU(alpha=0.2)(x)

    # add another Upsampling block (similar to the previous layer), except that the number of filters used in the convolution layer is 128
    x = UpSampling2D(size=(2, 2))(x)
    x = Conv2D(filters=64, kernel_size=5, padding='same')(x)
    x = BatchNormalization(momentum=0.8)(x)
    x = LeakyReLU(alpha=0.2)(x)

    # add the last Upsampling block. The configuration is similar to the previous layer, except for the the fact that there are three filters used in the convolution layer and batch
    # normalization is not used
    x = UpSampling2D(size=(2, 2))(x)
    x = Conv2D(filters=3, kernel_size=5, padding='same')(x)
    x = Activation('tanh')(x)

    # create a Keras model and specify the inputs and the outputs for the generator network
    model = Model(inputs=[input_z_noise, input_label], outputs=[x])
    return model

In [13]:
# The expand_label_input function
def expand_label_input(x):
    x = K.expand_dims(x, axis=1)
    x = K.expand_dims(x, axis=1)
    x = K.tile(x, [1, 32, 32, 1])
    return x

# The preceding function will transform a tensor with a dimension of (6, ) to a tensor with a dimension of (32, 32, 6)

In [14]:
def build_discriminator():
    """
    The discriminator network is a CNN
    Create a Discriminator Model with hyperparameters values defined as follows
    :return: Discriminator model
    """
    
    # creating two input layers, as our discriminator network will process two inputs
    # Specify hyperparameters
    # Input image shape
    input_shape = (64, 64, 3)
    # Input conditioning variable shape
    label_shape = (6,)
    # Two input layers
    image_input = Input(shape=input_shape)
    label_input = Input(shape=label_shape)

    # add a 2-D convolution block (Conv2D + Activation function)
    x = Conv2D(64, kernel_size=3, strides=2, padding='same')(image_input)
    x = LeakyReLU(alpha=0.2)(x)

    # expand label_input so that it has a shape of (32, 32, 6)
    label_input1 = Lambda(expand_label_input)(label_input)
    
    # concatenate the transformed label tensor and the output of the last convolution layer along the channel dimension
    x = concatenate([x, label_input1], axis=3)

    # Add a convolution block (2D convolution layer + batch normalization + activation function)
    x = Conv2D(128, kernel_size=3, strides=2, padding='same')(x)
    x = BatchNormalization()(x)
    x = LeakyReLU(alpha=0.2)(x)

    # add two more convolution blocks
    x = Conv2D(256, kernel_size=3, strides=2, padding='same')(x)
    x = BatchNormalization()(x)
    x = LeakyReLU(alpha=0.2)(x)

    x = Conv2D(512, kernel_size=3, strides=2, padding='same')(x)
    x = BatchNormalization()(x)
    x = LeakyReLU(alpha=0.2)(x)

    # add a flatten layer
    x = Flatten()(x)
    
    # add a dense layer (classification layer) that outputs a probability
    x = Dense(1, activation='sigmoid')(x)

    # create a Keras model and specify the inputs and outputs for the discriminator network
    model = Model(inputs=[image_input, label_input], outputs=[x])
    
    return model

In [15]:
# Training the cGAN for face aging is a three-step process:

#  Training the cGAN
#  Initial latent vector approximation
#  Latent vector optimization

In [16]:
#  Training the cGAN

# train the generator and the discriminator networks

In [17]:
# Start by specifying the parameters required for the training:

# Define hyperparameters
data_dir = "./"
wiki_dir = os.path.join(data_dir, "wiki_crop")

epochs = 500
batch_size = 128
image_shape = (64, 64, 3)
z_shape = 100

TRAIN_GAN = True
TRAIN_ENCODER = False
TRAIN_GAN_WITH_FR = False
fr_image_shape = (192, 192, 3)

In [18]:
print(wiki_dir)

./wiki_crop


In [19]:
# Define optimizers
# Optimizer for the discriminator network
dis_optimizer = tf.keras.optimizers.Adam(lr=0.0002, beta_1=0.5, beta_2=0.999, epsilon=10e-8)

# Optimizer for the generator network
gen_optimizer = tf.keras.optimizers.Adam(lr=0.0002, beta_1=0.5, beta_2=0.999, epsilon=10e-8)

# Optimizer for the adversarial network
adversarial_optimizer = tf.keras.optimizers.Adam(lr=0.0002, beta_1=0.5, beta_2=0.999, epsilon=10e-8)

/home/alejandro/anaconda3/envs/tensorflow2/lib/python3.8/site-packages/keras/optimizer_v2/adam.py:105: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super(Adam, self).__init__(name, **kwargs)


In [20]:
# load and compile the generator and the discriminator networks. In Keras, we must compile the networks before we train the networks

In [30]:
# Build and compile the discriminator network
discriminator = build_discriminator()
discriminator.compile(loss=['binary_crossentropy'], optimizer=dis_optimizer)

# Build and compile the generator network
generator = build_generator()
generator.compile(loss=['binary_crossentropy'], optimizer=gen_optimizer)

In [31]:
# Build and compile the adversarial model

discriminator.trainable = False
input_z_noise = Input(shape=(100,))
input_label = Input(shape=(6,))
recons_images = generator([input_z_noise, input_label])
valid = discriminator([recons_images, input_label])
adversarial_model = Model(inputs=[input_z_noise, input_label], outputs=[valid])
adversarial_model.compile(loss=['binary_crossentropy'], optimizer=gen_optimizer)

In [32]:
# add TensorBoard to store losses

tensorboard = TensorBoard(log_dir="logs/{}".format(time.time()))
tensorboard.set_model(generator)
tensorboard.set_model(discriminator)

In [33]:
# load all images using the load_data function

images, age_list = load_data(wiki_dir=wiki_dir, dataset="wiki")

In [34]:
# This method will convert age to respective category
def age_to_category(age_list):
    age_list1 = []

    for age in age_list:
        if 0 < age <= 18:
            age_category = 0
        elif 18 < age <= 29:
            age_category = 1
        elif 29 < age <= 39:
            age_category = 2
        elif 39 < age <= 49:
            age_category = 3
        elif 49 < age <= 59:
            age_category = 4
        elif age >= 60:
            age_category = 5

        age_list1.append(age_category)
    return age_list1

# The output of age_cat should look as follows:
# [1, 2, 4, 2, 3, 4, 2, 5, 5, 1, 3, 2, 1, 1, 2, 1, 2, 2, 1, 5, 4 , .............]

In [35]:
# Convert age to category

age_cat = age_to_category(age_list)

In [36]:
# Convert the age categories to one-hot encoded vectors:

# Also, convert the age categories to one-hot encoded vectors

final_age_cat = np.reshape(np.array(age_cat), [len(age_cat), 1])
classes = len(set(age_cat))
y = tf.keras.utils.to_categorical(final_age_cat, num_classes=len(set(age_cat)))

In [37]:
y

array([[0., 1., 0., 0., 0., 0.],
       [0., 0., 1., 0., 0., 0.],
       [0., 0., 0., 0., 1., 0.],
       ...,
       [0., 0., 0., 1., 0., 0.],
       [0., 1., 0., 0., 0., 0.],
       [0., 0., 0., 0., 1., 0.]], dtype=float32)

In [38]:
y.shape

(62328, 6)

In [39]:
def load_images(data_dir, image_paths, image_shape):
    images = None

    for i, image_path in enumerate(image_paths):
        print()
        try:
            # Load image
            loaded_image = tf.keras.preprocessing.image.load_img(os.path.join(data_dir, image_path), target_size=image_shape)

            # Convert PIL image to numpy ndarray
            loaded_image = tf.keras.preprocessing.image.img_to_array(loaded_image)

            # Add another dimension (Add batch dimension)
            loaded_image = np.expand_dims(loaded_image, axis=0)

            # Concatenate all images into one tensor
            if images is None:
                images = loaded_image
            else:
                images = np.concatenate([images, loaded_image], axis=0)
        except Exception as e:
            print("Error:", i, e)

    return images

In [40]:
print(type(images))
print(images[0])
print(wiki_dir)

<class 'list'>
17/10000217_1981-05-05_2009.jpg
./wiki_crop


In [41]:
# tf.keras.preprocessing.image.DirectoryIterator(
#     directory, image_data_generator, target_size=(256, 256),
#     color_mode='rgb', classes=None, class_mode='categorical',
#     batch_size=32, shuffle=True, seed=None, data_format=None, save_to_dir=None,
#     save_prefix='', save_format='png', follow_links=False,
#     subset=None, interpolation='nearest', dtype=None
# )

In [42]:
# Read all images and create an ndarray
loaded_images = load_images(wiki_dir, images, (image_shape[0], image_shape[1]))


Error: 0 [Errno 2] No such file or directory: './wiki_crop/17/10000217_1981-05-05_2009.jpg'

Error: 1 [Errno 2] No such file or directory: './wiki_crop/48/10000548_1925-04-04_1964.jpg'

Error: 2 [Errno 2] No such file or directory: './wiki_crop/12/100012_1948-07-03_2008.jpg'

Error: 3 [Errno 2] No such file or directory: './wiki_crop/65/10001965_1930-05-23_1961.jpg'

Error: 4 [Errno 2] No such file or directory: './wiki_crop/16/10002116_1971-05-31_2012.jpg'

Error: 5 [Errno 2] No such file or directory: './wiki_crop/02/10002702_1960-11-09_2012.jpg'

Error: 6 [Errno 2] No such file or directory: './wiki_crop/41/10003541_1937-09-27_1971.jpg'

Error: 7 [Errno 2] No such file or directory: './wiki_crop/39/100039_1904-12-07_1982.jpg'

Error: 8 [Errno 2] No such file or directory: './wiki_crop/13/10004113_1946-08-26_2007.jpg'

Error: 9 [Errno 2] No such file or directory: './wiki_crop/22/10004122_1982-03-17_2011.jpg'

Error: 10 [Errno 2] No such file or directory: './wiki_crop/99/10004299_1

In [43]:
loaded_images